In [67]:
# import geopandas as gpd
# import geopy
# from shapely.geometry import Point
# from geopy.geocoders import Nominatim

import pandas as pd
import numpy as np
import mpu

pd.set_option('display.max_rows', 10000)
pd.set_option('display.max_columns', 10000)
pd.set_option('display.width', 10000)


In [68]:
df = pd.read_excel('atm_bank_misr.xlsx')
#df.head()
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4263 entries, 0 to 4262
Data columns (total 6 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   ID           4263 non-null   int64  
 1   governerate  4263 non-null   object 
 2   region       4263 non-null   object 
 3   Address      4263 non-null   object 
 4   Lat          4263 non-null   float64
 5   Long         4263 non-null   float64
dtypes: float64(2), int64(1), object(3)
memory usage: 200.0+ KB


In [69]:
df.head()

ID governerate            region                                        Address        Lat       Long
0   1   Al Fayyum  Markaz Al-Fayyum                  Alfayoum Beghous Alhoriea St.  29.304412  30.853546
1   2   Al Fayyum  Markaz Al-Fayyum                              Fayoum University  29.319696  30.835641
2   3   Al Fayyum  Markaz Al-Fayyum                            Fayoum AlHoriea St.  29.308199  30.842229
3   4   Al Fayyum   Markaz Sinnuris                               Sanoras - Fayoum  29.408575  30.865073
4   5   Al Fayyum       Markaz Itsa  194 Abo Bakr AlSiddiq St.- Atsa City - Fayoum  29.236966  30.790194

In [70]:
df.iloc[[55,132]]

ID  governerate             region                     Address        Lat      Long
55    56  Al Buhayrah  Markaz Abu Hummus  The local unit - Abo Homos  31.100602  30.31555
132  133  Al Buhayrah  Markaz Abu Hummus  The local unit - Abo Homos  31.100602  30.31555

In [71]:
lat_longs = np.array(df[['Lat','Long']])#

In [72]:
df

ID       governerate                                             region                                            Address        Lat       Long
0        1         Al Fayyum                                   Markaz Al-Fayyum                      Alfayoum Beghous Alhoriea St.  29.304412  30.853546
1        2         Al Fayyum                                   Markaz Al-Fayyum                                  Fayoum University  29.319696  30.835641
2        3         Al Fayyum                                   Markaz Al-Fayyum                                Fayoum AlHoriea St.  29.308199  30.842229
3        4         Al Fayyum                                    Markaz Sinnuris                                   Sanoras - Fayoum  29.408575  30.865073
4        5         Al Fayyum                                        Markaz Itsa      194 Abo Bakr AlSiddiq St.- Atsa City - Fayoum  29.236966  30.790194
5        6         Al Fayyum                                   Markaz Al-Fayyum                   AlFayoum 45 AlHorreya St. Fayoum  29.307723  30.846140
6        7         Al Fayyum                                   Markaz Al-Fayyum     Gamal Abd AlNasser St. - AlMasalla Sq.- Fayoum  29.315420  30.852179
7        8         Al Fayyum                                   Markaz Al-Fayyum               10th of Ramadan - Industrial Zone B1  29.321487  30.837896
8        9         Al Fayyum                                   Markaz Al-Fayyum                  Faculty of Arts Fayoum University  29.322145  30.837087
9       10         Al Fayyum                                   Markaz Al-Fayyum                               Fayoum train station  29.308889  30.847499
10      11         Al Fayyum                                   Markaz Al-Fayyum                          Batal Alsalam St.- Fayoum  29.304818  30.843850
11      12         Al Fayyum                                    Markaz Ibshaway                            AlGomhoria St. Ibshaway  29.370735  30.688374
12      13         Al Fayyum                                   Markaz Al-Fayyum                                  Saad Zaghloul St.  29.319011  30.851452
13      14         Al Fayyum                                    Markaz Ibshaway  Algomhoria St. in front of Ibshaway Fayoum Pos...  29.360741  30.683258
14      15         Al Fayyum                                   Markaz Al-Fayyum  B 32 Almasalah Sq. Faioum Bandar Alfaioum Gove...  29.315635  30.852531
15      16         Al Fayyum                                     Markaz Tamiyah          23rd of July St. - Tamiya Center - Fayoum  29.474276  30.954961
16      17         Al Fayyum                                    Markaz Sinnuris              Almadares St. Sanoras Sector Alfaioum  29.408703  30.858720
17      18         Al Fayyum                                   Markaz Al-Fayyum  Jamal Abdel Nasser Street, behind the local po...  29.309736  30.847641
18      19         Al Fayyum                                    Markaz Sinnuris            Tersa Village - Senoras Center - Fayoum  29.417200  30.817362
19      20         Al Fayyum                                    Markaz Sinnuris         Vidimin Village - Senoures Center - Fayoum  29.381256  30.777553
20      21         Al Fayyum                                    Markaz Sinnuris         Naqalifa Village - Senoras Sector - Fayoum  29.396940  30.824684
21      22         Al Fayyum                                   Markaz Al-Fayyum    12 Khaled Bin Al Waleed Street, Baghous, Fayoum  29.302993  30.852963
22      23         Al Fayyum                                        Markaz Itsa  Governor of Fayoum - Abu Jandir - Atsa Center ...  29.241247  30.672294
23      24         Al Fayyum                                   Markaz Al-Fayyum  Hospital Street next to Lahoun Hospital and Ag...  29.209594  30.971382
24      25         Al Fayyum                                    Markaz Sinnuris  Fayoum - in front of the Society for the Prese...  29.407404  30.770053
25      26         Al Fayyum  

In [73]:
k = 4


near_dis1 = [] # distance of nearest atm
index1 = [] # index of nearest atm

near_dis2 = []
index2 = []

near_dis3 = []
index3 = []

for i in range(len(lat_longs)):
    err_list = []
    
    for j in range(len(lat_longs)): 
        
        lat1,lon1,lat2,lon2 = lat_longs[i][0],lat_longs[i][1],lat_longs[j][0],lat_longs[j][1]
        err_list.append(mpu.haversine_distance((lat1, lon1), (lat2, lon2)))
    
    distances = np.array(err_list)
    least_k = np.argsort(distances)[1:k]
    print('Indexes of nearest lat_long',least_k)
    print('For lat_long',lat_longs[i],'the nearest lat_longs are:')
    print(lat_longs[least_k])
    print('With distances of:') 
    print(distances[least_k])
    
    least_k_distances = distances[least_k]
    near_dis1.append(least_k_distances[0])
    index1.append(least_k[0])
    near_dis2.append(least_k_distances[1])
    index2.append(least_k[1])
    near_dis3.append(least_k_distances[2])
    index3.append(least_k[2])
    print('-------------------------------------')
    
    
    
    
    

Indexes of nearest lat_long [21 29  9]
For lat_long [29.30441208 30.85354563] the nearest lat_longs are:
[[29.3029927  30.85296321]
 [29.308889   30.847499  ]
 [29.308889   30.847499  ]]
With distances of:
[0.1676278  0.76913315 0.76913315]
-------------------------------------
Indexes of nearest lat_long [32  7 31]
For lat_long [29.319696 30.835641] the nearest lat_longs are:
[[29.319696 30.835641]
 [29.321487 30.837896]
 [29.322145 30.837087]]
With distances of:
[0.         0.29573057 0.30628301]
-------------------------------------
Indexes of nearest lat_long [ 2  5 35]
For lat_long [29.308199 30.842229] the nearest lat_longs are:
[[29.308199   30.842229  ]
 [29.30772267 30.84613982]
 [29.304818   30.84385   ]]
With distances of:
[0.         0.38288298 0.40748412]
-------------------------------------
Indexes of nearest lat_long [16 25 20]
For lat_long [29.40857519 30.86507307] the nearest lat_longs are:
[[29.4087034  30.8587204 ]
 [29.41540081 30.86429428]
 [29.39694049 30.8246841

Indexes of nearest lat_long [1289 1288 1310]
For lat_long [29.07578529 31.09938927] the nearest lat_longs are:
[[29.07578529 31.09938927]
 [29.07523208 31.09924149]
 [29.07535899 31.09829712]]
With distances of:
[5.31824916e-07 6.31679329e-02 1.16241722e-01]
-------------------------------------
Indexes of nearest lat_long [ 190   43 3350]
For lat_long [31.10691837 30.64172916] the nearest lat_longs are:
[[31.10958367 30.63910172]
 [31.103395   30.638362  ]
 [31.12534257 30.64901408]]
With distances of:
[0.38782124 0.50622396 2.16287267]
-------------------------------------
Indexes of nearest lat_long [ 46 153  84]
For lat_long [30.9135036  30.29365764] the nearest lat_longs are:
[[30.912765 30.295561]
 [30.912765 30.295561]
 [30.915766 30.297315]]
With distances of:
[0.19928897 0.19928897 0.43013985]
-------------------------------------
Indexes of nearest lat_long [ 40 177 128]
For lat_long [31.024659 30.607641] the nearest lat_longs are:
[[31.024659   30.607641  ]
 [31.02393382 30.

Indexes of nearest lat_long [ 75 119 106]
For lat_long [31.03450281 30.47469798] the nearest lat_longs are:
[[31.03449464 30.47471262]
 [31.03428061 30.46823018]
 [31.041921   30.473102  ]]
With distances of:
[0.00166475 0.61673596 0.83876286]
-------------------------------------
Indexes of nearest lat_long [ 74 119 106]
For lat_long [31.03449464 30.47471262] the nearest lat_longs are:
[[31.03450281 30.47469798]
 [31.03428061 30.46823018]
 [31.041921   30.473102  ]]
With distances of:
[0.00166475 0.61809378 0.83991061]
-------------------------------------
Indexes of nearest lat_long [140 109 136]
For lat_long [31.04241948 30.46890924] the nearest lat_longs are:
[[31.04241948 30.46890924]
 [31.040307   30.468207  ]
 [31.040307   30.468207  ]]
With distances of:
[5.25693289e-07 2.44238639e-01 2.44238639e-01]
-------------------------------------
Indexes of nearest lat_long [196 112  64]
For lat_long [30.81405902 29.98830245] the nearest lat_longs are:
[[30.92230447 29.95121672]
 [30.86

Indexes of nearest lat_long [113  48 161]
For lat_long [30.8601142  30.15493118] the nearest lat_longs are:
[[30.9063534 30.1736873]
 [30.912211  30.170589 ]
 [30.912211  30.170589 ]]
With distances of:
[5.44420412 5.9824931  5.9824931 ]
-------------------------------------
Indexes of nearest lat_long [193  73 114]
For lat_long [30.9063534 30.1736873] the nearest lat_longs are:
[[30.91144225 30.17490715]
 [30.91078908 30.17701905]
 [30.91158881 30.17717889]]
With distances of:
[0.57769797 0.5867773  0.67071759]
-------------------------------------
Indexes of nearest lat_long [ 73 192 193]
For lat_long [30.91158881 30.17717889] the nearest lat_longs are:
[[30.91078908 30.17701905]
 [30.91290404 30.17689168]
 [30.91144225 30.17490715]]
With distances of:
[0.09022356 0.1487915  0.21733809]
-------------------------------------
Indexes of nearest lat_long [169 101  49]
For lat_long [30.82974495 30.52961337] the nearest lat_longs are:
[[30.833752 30.530286]
 [30.833752 30.530286]
 [30.829

Indexes of nearest lat_long [149  61 189]
For lat_long [31.036522 30.456495] the nearest lat_longs are:
[[31.036522 30.456495]
 [31.036388 30.457638]
 [31.036388 30.457638]]
With distances of:
[0.         0.10991531 0.10991531]
-------------------------------------
Indexes of nearest lat_long [ 57 119 189]
For lat_long [31.032701 30.464771] the nearest lat_longs are:
[[31.032701   30.464771  ]
 [31.03428061 30.46823018]
 [31.036388   30.457638  ]]
With distances of:
[0.         0.37346905 0.79370128]
-------------------------------------
Indexes of nearest lat_long [151  78 153]
For lat_long [30.915766 30.297315] the nearest lat_longs are:
[[30.915766   30.297315  ]
 [30.91770833 30.30043628]
 [30.912765   30.295561  ]]
With distances of:
[0.         0.36783874 0.37329859]
-------------------------------------
Indexes of nearest lat_long [ 40 177 128]
For lat_long [31.024659 30.607641] the nearest lat_longs are:
[[31.024659   30.607641  ]
 [31.02393382 30.60350721]
 [31.013742   30.570

...

Indexes of nearest lat_long [4036 3975 4002]
For lat_long [26.74542573 31.61892827] the nearest lat_longs are:
[[26.700333   31.606733  ]
 [26.69677484 31.60331427]
 [26.69671523 31.60334293]]
With distances of:
[5.15830084 5.62762151 5.63321114]
-------------------------------------
Indexes of nearest lat_long [4038 3971 4107]
For lat_long [26.63916034 31.63109942] the nearest lat_longs are:
[[26.620603 31.641827]
 [26.658164 31.666661]
 [26.658164 31.666661]]
With distances of:
[2.32271107 4.11775979 4.11775979]
-------------------------------------
Indexes of nearest lat_long [3985 3979 4113]
For lat_long [26.82980015 31.49127052] the nearest lat_longs are:
[[26.828038   31.492542  ]
 [26.825789   31.495771  ]
 [26.84602672 31.47678155]]
With distances of:
[0.23304624 0.6311546  2.30697484]
-------------------------------------
Indexes of nearest lat_long [4068 4023 3994]
For lat_long [26.73394621 31.46292606] the nearest lat_longs are:
[[26.72577169 31.49888664]
 [26.770098   31.49

Indexes of nearest lat_long [4182 4218 4119]
For lat_long [27.90947216 34.32567521] the nearest lat_longs are:
[[27.906941 34.326242]
 [27.90764  34.319536]
 [27.90764  34.319536]]
With distances of:
[0.28690962 0.63672642 0.63672642]
-------------------------------------
Indexes of nearest lat_long [4122 4201 4216]
For lat_long [27.875407 34.318455] the nearest lat_longs are:
[[27.873564   34.317922  ]
 [27.87905743 34.31821842]
 [27.866018   34.319858  ]]
With distances of:
[0.211523   0.40657483 1.05307855]
-------------------------------------
Indexes of nearest lat_long [4121 4201 4216]
For lat_long [27.873564 34.317922] the nearest lat_longs are:
[[27.875407   34.318455  ]
 [27.87905743 34.31821842]
 [27.866018   34.319858  ]]
With distances of:
[0.211523 0.611536 0.860387]
-------------------------------------
Indexes of nearest lat_long [4168 4160 4213]
For lat_long [29.5902404 32.7222317] the nearest lat_longs are:
[[29.593128   32.716771  ]
 [29.589836   32.706426  ]
 [29.835

Indexes of nearest lat_long [4146 4157 4194]
For lat_long [27.915316 34.326139] the nearest lat_longs are:
[[27.917054 34.328564]
 [27.915035 34.32957 ]
 [27.915035 34.32957 ]]
With distances of:
[0.30679088 0.33856286 0.33856286]
-------------------------------------
Indexes of nearest lat_long [4183 4131 4186]
For lat_long [27.965667 34.400117] the nearest lat_longs are:
[[27.965728   34.4001    ]
 [27.96176668 34.39366307]
 [27.96167626 34.39360834]]
With distances of:
[0.00698535 0.76802681 0.77815832]
-------------------------------------
Indexes of nearest lat_long [4168 4123 4213]
For lat_long [29.589836 32.706426] the nearest lat_longs are:
[[29.593128   32.716771  ]
 [29.5902404  32.7222317 ]
 [29.835331   32.66745035]]
With distances of:
[ 1.06514993  1.52896189 27.55609011]
-------------------------------------
Indexes of nearest lat_long [4126 4130 4116]
For lat_long [29.058725 33.101453] the nearest lat_longs are:
[[29.047371   33.103307  ]
 [29.04933907 33.12174976]
 [28.

Indexes of nearest lat_long [4197 4196 4206]
For lat_long [27.926445 34.34171 ] the nearest lat_longs are:
[[27.926445   34.34171   ]
 [27.92644461 34.34171012]
 [27.92371498 34.34049953]]
With distances of:
[0.00000000e+00 4.49400184e-05 3.26028573e-01]
-------------------------------------
Indexes of nearest lat_long [4145 4220 4194]
For lat_long [27.91600977 34.33010774] the nearest lat_longs are:
[[27.91601  34.330108]
 [27.91601  34.330108]
 [27.915035 34.32957 ]]
With distances of:
[3.61482364e-05 3.61482364e-05 1.20581715e-01]
-------------------------------------
Indexes of nearest lat_long [4115 4138 4189]
For lat_long [28.05988781 34.43373922] the nearest lat_longs are:
[[28.052412 34.434505]
 [28.034812 34.435745]
 [28.034812 34.435745]]
With distances of:
[0.83466165 2.79524213 2.79524213]
-------------------------------------
Indexes of nearest lat_long [4143 4219 4142]
For lat_long [28.02199792 34.42694838] the nearest lat_longs are:
[[28.019413 34.433778]
 [28.019435 34.

Indexes of nearest lat_long [4238 4236 4260]
For lat_long [29.72885  32.381612] the nearest lat_longs are:
[[29.72885   32.381612 ]
 [29.6702975 32.3177524]
 [29.617352  32.31746  ]]
With distances of:
[ 0.          8.96854045 13.86091873]
-------------------------------------
Indexes of nearest lat_long [4239 4236 4242]
For lat_long [29.617352 32.31746 ] the nearest lat_longs are:
[[29.617352  32.31746  ]
 [29.6702975 32.3177524]
 [29.642807  32.211749 ]]
With distances of:
[ 0.          5.88733825 10.60225721]
-------------------------------------
Indexes of nearest lat_long [4249 4228 4237]
For lat_long [30.059608 32.410829] the nearest lat_longs are:
[[30.059608   32.410829  ]
 [29.99219379 32.49470298]
 [29.98951717 32.52027418]]
With distances of:
[ 0.         11.01787053 13.10589573]
-------------------------------------
Indexes of nearest lat_long [4250 4237 4262]
For lat_long [29.989186 32.527362] the nearest lat_longs are:
[[29.989186   32.527362  ]
 [29.98951717 32.52027418]

In [45]:
nearest_df = df.iloc[index1]

In [ ]:
near_dis1 = [float( '%.3f'%(x)) for x in near_dis1]
near_dis1

In [76]:
new_df = pd.concat([df.reset_index(drop=True),nearest_df.reset_index(drop=True)], axis=1)


In [77]:
new_df.drop('indexes',axis = 1,inplace= True)

new_df['distance'] = near_dis1

In [78]:
new_df

ID       governerate                                             region                                            Address        Lat       Long    ID       governerate                                             region                                            Address        Lat       Long  distance
0        1         Al Fayyum                                   Markaz Al-Fayyum                      Alfayoum Beghous Alhoriea St.  29.304412  30.853546    22         Al Fayyum                                   Markaz Al-Fayyum    12 Khaled Bin Al Waleed Street, Baghous, Fayoum  29.302993  30.852963     0.168
1        2         Al Fayyum                                   Markaz Al-Fayyum                                  Fayoum University  29.319696  30.835641    33         Al Fayyum                                   Markaz Al-Fayyum                                  Fayoum University  29.319696  30.835641     0.000
2        3         Al Fayyum                                   Markaz Al-Fayyum                                Fayoum AlHoriea St.  29.308199  30.842229     3         Al Fayyum                                   Markaz Al-Fayyum                                Fayoum AlHoriea St.  29.308199  30.842229     0.000
3        4         Al Fayyum                                    Markaz Sinnuris                                   Sanoras - Fayoum  29.408575  30.865073    17         Al Fayyum                                    Markaz Sinnuris              Almadares St. Sanoras Sector Alfaioum  29.408703  30.858720     0.616
4        5         Al Fayyum                                        Markaz Itsa      194 Abo Bakr AlSiddiq St.- Atsa City - Fayoum  29.236966  30.790194    29         Al Fayyum                                        Markaz Itsa  Omar Ibn Al-Khattab Street - next to the local...  29.237697  30.795299     0.502
5        6         Al Fayyum                                   Markaz Al-Fayyum                   AlFayoum 45 AlHorreya St. Fayoum  29.307723  30.846140    30         Al Fayyum                                   Markaz Al-Fayyum                               Fayoum train station  29.308889  30.847499     0.185
6        7         Al Fayyum                                   Markaz Al-Fayyum     Gamal Abd AlNasser St. - AlMasalla Sq.- Fayoum  29.315420  30.852179    15         Al Fayyum                                   Markaz Al-Fayyum  B 32 Almasalah Sq. Faioum Bandar Alfaioum Gove...  29.315635  30.852531     0.042
7        8         Al Fayyum                                   Markaz Al-Fayyum               10th of Ramadan - Industrial Zone B1  29.321487  30.837896    32         Al Fayyum                                   Markaz Al-Fayyum                  Faculty of Arts Fayoum University  29.322145  30.837087     0.107
8        9         Al Fayyum                                   Markaz Al-Fayyum                  Faculty of Arts Fayoum University  29.322145  30.837087     9         Al Fayyum                                   Markaz Al-Fayyum                  Faculty of Arts Fayoum University  29.322145  30.837087     0.000
9       10         Al Fayyum                                   Markaz Al-Fayyum                               Fayoum train station  29.308889  30.847499    10         Al Fayyum                                   Markaz Al-Fayyum                               Fayoum train station  29.308889  30.847499     0.000
10      11         Al Fayyum                                   Markaz Al-Fayyum                          Batal Alsalam St.- Fayoum  29.304818  30.843850    36         Al Fayyum                                   Markaz Al-Fayyum                          Batal Alsalam St.- Fayoum  29.304818  30.843850     0.000
11      12         Al Fayyum                                    Markaz Ibshaway                            AlGomhoria St. Ibshaway  29.370735  30.688374    12         Al Fayyum                                    Markaz Ibshaway                            AlGomhoria St. Ibshaw

In [79]:
new_df.to_excel('nearest_atm1.xlsx')

In [ ]:
#Id1 | address1 | gov1 | section1 | lat1 | long1 | ---- | Id2 | address | gov | section | lat | long  | Id2 | address | gov | section | lat | long | Id2 | address | gov | section | lat | long